In [1]:
library("dplyr")
library("leaflet")
library("osmdata")
library("sf")
library("sfnetworks")
library("tidygraph")


Caricamento pacchetto: ‘dplyr’


I seguenti oggetti sono mascherati da ‘package:stats’:

    filter, lag


I seguenti oggetti sono mascherati da ‘package:base’:

    intersect, setdiff, setequal, union


Warning message:
“il pacchetto ‘leaflet’ è stato creato con R versione 4.3.2”
Data (c) OpenStreetMap contributors, ODbL 1.0. https://www.openstreetmap.org/copyright

Warning message:
“il pacchetto ‘sf’ è stato creato con R versione 4.3.2”
Linking to GEOS 3.11.0, GDAL 3.5.3, PROJ 9.1.0; sf_use_s2() is TRUE

Warning message:
“il pacchetto ‘sfnetworks’ è stato creato con R versione 4.3.2”
Warning message:
“il pacchetto ‘tidygraph’ è stato creato con R versione 4.3.2”

Caricamento pacchetto: ‘tidygraph’


Il seguente oggetto è mascherato da ‘package:stats’:

    filter




# Corridor edges

In this notebooks we explore how to delineate river corridor edges using Bucharest as the study area.

In [2]:
# bounding box
bb <- getbb("Bucharest")

We focus on one of the rivers and use the following projected CRS for the analysis:

In [3]:
river_name <- "Dâmbovița"
epsg_code <- 32635  # UTM zone 35N

A couple of utility functions:

In [4]:
# query the Overpass API for a key:value pair and a bounding box
osmdata_as_sf <- function(key, value, bb){
    bb |>
        opq() |>
        add_osm_feature(key = key, value = value) |>
        osmdata_sf()
}

In [5]:
# get geometry in lat/lon (WGS84)
getGeomLatLon <- function(x) st_transform(x, 4326) |> st_geometry() 

## 1. Initial corridor edge

While ideally we want to base the initial estimate of the corridor edge on the basis of the river valley delineation, we use here the roughest approach of defining a buffer region around the waterways. This method could actually be the method of choice for flat cities. 

### Waterways

Querying the Overpass API for `waterway:river`:

In [6]:
# waterways (linestrings)
waterways <- osmdata_as_sf("waterway", "river", bb)

In [7]:
waterways$osm_multilines

Registered S3 method overwritten by 'geojsonsf':
  method        from   
  print.geojson geojson



osm_id  name      role      destination type     waterway
6213642-(no role) 6213642 Pasărea   (no role) Dâmbovița   waterway river   
6213935-(no role) 6213935 Dâmbovița (no role)             waterway river   
6214017-(no role) 6214017 Colentina (no role) Dâmbovița   waterway river   
                  wikidata wikipedia                 
6213642-(no role) Q7143173 ro:Râul Pasărea, Dâmbovița
6213935-(no role) Q214646  ro:Râul Dâmbovița         
6214017-(no role) Q1108116 ro:Râul Colentina         
                  geometry                      
6213642-(no role) MULTILINESTRING ((26.01958 ...
6213935-(no role) MULTILINESTRING ((24.95921 ...
6214017-(no role) MULTILINESTRING ((25.65092 ...

OSM multilines include river lines grouped by the river name.

In [9]:
leaflet() |>
    addTiles() |> 
    addPolylines(data = getGeomLatLon(waterways$osm_multilines), color="blue")

HTML widgets cannot be represented in plain text (need html)

### Water

Querying the Overpass API for `natural:water`: 

In [10]:
# water area (polygons)
water <- osmdata_as_sf("natural", "water", bb)

In [12]:
leaflet() |>
    addTiles() |> 
    addPolylines(data = getGeomLatLon(water$osm_lines), color="blue", group="osm_lines") |>
    addPolygons(data = getGeomLatLon(water$osm_polygons), color="red", group="osm_polygons") |> 
    addPolygons(data = getGeomLatLon(water$osm_multipolygons), color="black", group="osm_multipolygons") |>
    addLayersControl(overlayGroups=c("osm_lines", "osm_polygons", "osm_multipolygons"))

HTML widgets cannot be represented in plain text (need html)

The results of the query with tag `natural:water` also include features such as fountains. The geometries are not contiguous and some part of the water bodies are actually represented as lines instead of polygons. So some more data filtering and cleaning would be required for this tag - using the waterway + buffer for now.

### Constructing the initial corridor

In order to buffer, we transform the rivers to the projected CRS:

In [13]:
buffer_dist <- 500  # distance (in m) from the water stream

In [14]:
corridor_initial <- waterways$osm_multilines |>
    st_transform(epsg_code) |>
    st_buffer(buffer_dist) |>
    filter(name == river_name) |> 
    st_geometry()

In [15]:
leaflet() |>
    addTiles() |>
    addPolygons(data = getGeomLatLon(corridor_initial))

HTML widgets cannot be represented in plain text (need html)

## 2. Street network

Querying the Overpass API for the `highway` key:

In [16]:
highways_value <- c("motorway", "primary", "secondary", "tertiary")
highways <- osmdata_as_sf("highway", highways_value, bb)

We use `sfnetworks` to setup the street network based on the OSM data, mostly following [this tutorial](https://geospatial-community.netlify.app/post/2022-03-31-spatial-networks/) for data cleaning and network setup.

In [17]:
# cast polygons (closed streets) into lines
poly_to_lines <- highways$osm_polygons |>
    st_cast("LINESTRING")
highways_lines <- highways$osm_lines |>
    bind_rows(poly_to_lines)

Warning message in st_cast.sf(highways$osm_polygons, "LINESTRING"):
“repeating attributes for all sub-geometries for which they may not be constant”


In [19]:
# create network, only keeping "highway" column
net <- highways_lines |> 
    select("highway") |>
    as_sfnetwork(directed = FALSE)

In [74]:
filtered <- net |> 
    activate("nodes") |> 
    filter(!st_intersects(geometry, corridor_initial |> st_transform(st_crs(net)), sparse = FALSE)) |> 
    activate("edges") |> 
    filter(!st_intersects(geometry, corridor_initial |> st_transform(st_crs(net)), sparse = FALSE))

In [76]:
# create simple graph (no loops, no double-edge connections)
# https://luukvdmeer.github.io/sfnetworks/articles/sfn02_preprocess_clean.html#simplify-network
simple <- filtered |>
  activate("edges") |>
  # reorder so that only shortest edge is kept
  arrange(edge_length()) |>
  filter(!edge_is_multiple()) |>
  filter(!edge_is_loop())

In [77]:
# subdivide edges (create missing nodes)
# https://luukvdmeer.github.io/sfnetworks/articles/sfn02_preprocess_clean.html#subdivide-edges
subdivision <- convert(simple, to_spatial_subdivision)

Warning message:
“to_spatial_subdivision assumes attributes are constant over geometries”


In [78]:
# smooth pseudo nodes
# https://luukvdmeer.github.io/sfnetworks/articles/sfn02_preprocess_clean.html#smooth-pseudo-nodes
smoothed <- convert(subdivision, to_spatial_smooth)

In [82]:
getNodes <- function(net) net |> activate("nodes") |> st_as_sf()
getEdges <- function(net) net |> activate("edges") |> as_tibble() 

leaflet() |>
    addTiles() |>
    addPolylines(data = getEdges(smoothed) |> getGeomLatLon(), color = "black") |>
    addCircles(data = getNodes(smoothed) |> getGeomLatLon(), color = "red") |>
    addPolygons(data = getGeomLatLon(corridor_initial), color = "blue")

HTML widgets cannot be represented in plain text (need html)

## 3. Corridor edge delineation

Find the end points:

In [123]:
# create boundary line using bbox
# alternative approach: find center and draw circumference at given radius
bbox <- bb |> as.vector() 
names(bbox) <- c("xmin", "ymin", "xmax", "ymax")
boundary <- st_bbox(bbox, crs = st_crs(4326)) |> 
    st_as_sfc() |> 
    st_boundary() |> 
    st_transform(epsg_code)

In [125]:
targets <- boundary |> 
    st_intersection(corridor_initial) |>
    # this is a multilinestring, break down complonents
    st_cast("LINESTRING") |> 
    st_centroid()

In [129]:
smoothed |> 

# A sfnetwork with 1960 nodes and 2799 edges
#
# CRS:  EPSG:4326 
#
# An undirected multigraph with 76 components with spatially explicit edges
#
# A tibble: 2,799 × 5
   from    to highway   .tidygraph_edge_index                           geometry
  <int> <int> <chr>     <list>                                  <LINESTRING [°]>
1     2     3 primary   <int [1]>             (26.07251 44.47779, 26.07253 44.4…
2     6     7 tertiary  <int [1]>             (26.05545 44.54042, 26.05546 44.5…
3     8     9 primary   <int [1]>             (26.10265 44.43564, 26.10263 44.4…
4    10    11 primary   <int [1]>             (26.061 44.42901, 26.06102 44.429)
5    13    14 secondary <int [1]>             (26.14342 44.45565, 26.14344 44.4…
6    15    16 secondary <int [1]>             (26.15754 44.4444, 26.15755 44.44…
# ℹ 2,793 more rows
#
# A tibble: 1,960 × 2
             geometry .tidygraph_node_index
          <POINT [°]>                 <int>
1 (26.06134 44.42893)                     2
2 (26.07

In [126]:
leaflet() |>
    addTiles() |>
    # addPolylines(data = getEdges(smoothed) |> getGeomLatLon(), color = "black") |>
    # addCircles(data = getNodes(smoothed) |> getGeomLatLon(), color = "red") |>
    addCircles(data = getGeomLatLon(targets), color = "red") |>
    addPolygons(data = getGeomLatLon(corridor_initial), color = "blue")

HTML widgets cannot be represented in plain text (need html)